In [1]:
import rasterio as rio
import geopandas as gpd
import fiona
import os
import pickle
# enable kml file reading for geopandas
from shapely.geometry import box, Polygon
import pandas as pd
import numpy as np
import leafmap.foliumap as leafmap # use folium backend
import rioxarray as rioxr
from typing import List, Union, Dict
fiona.drvsupport.supported_drivers['KML'] = 'rw'

pd.options.display.max_columns = 50

In [2]:
CRS = 32629

In [3]:
project_path = os.path.expanduser("/home/rustt/Documents/Projects/building_damage")

In [4]:
out_dir_path = os.path.join(project_path, "Data/processed")
raw_data_path = os.path.join(project_path, "Data/raw")
town_loc_path = os.path.join(raw_data_path, "villages_location/Earthquake_marocco_town.kml")

In [5]:
def make_path(file_name, dir=out_dir_path):
    return os.path.join(dir, file_name)

def save_pickle(data, output_path):
    with open(output_path, 'wb') as f:
        pickle.dump(data, f)
        
def load_pickle(path):
    with open(path, 'rb') as f:
        data = pickle.load(f)
    return data

In [6]:
def get_coords_point_geometry(geometry):
    """return list [lat, lon]"""
    return list(np.stack([geometry.values.y.squeeze() , geometry.values.x.squeeze()]))

In [7]:
town_test = "Tafeghaghte"
date_event = '2023-09-09'

In [8]:
# town = gpd.read_file(town_loc_path, driver='KML').to_crs(CRS)
# town.columns = [_.lower() for _ in town.columns]
# town = town.rename({"name":"town_name"}, axis=1).drop("description", axis=1)
# town["geometry"] = gpd.GeoSeries(gpd.points_from_xy(x=town.geometry.x, y=town.geometry.y))
# town.to_file(make_path("marocco_town.shp", raw_data_path))
town = gpd.read_file(make_path("marocco_town.shp", raw_data_path))

In [9]:
town

town_name                        geometry
0      Adassil  POINT (547909.130 3441974.137)
1  Tafeghaghte  POINT (573971.703 3451595.559)
2       Mejdid  POINT (548561.849 3442843.085)
3         Amzi  POINT (575844.024 3451538.007)
4      Tinzert  POINT (594423.730 3451056.954)
5    Taroudant  POINT (512035.792 3371260.816)

In [10]:
columns = load_pickle(make_path("mapping_columns_stac_collection.pkl", out_dir_path))
maxar_items = gpd.read_file(make_path("maxar_stac_items.shp", out_dir_path)).rename(columns, axis=1)

In [11]:
maxar_items = maxar_items.assign(
    after_event=(maxar_items.datetime > date_event)*1
)

In [12]:
maxar_items

id  \
0     29/031313133311/04eddade-a2dc-4d16-8710-fb764d...   
1     29/031313311112/04eddade-a2dc-4d16-8710-fb764d...   
2     29/031313133301/04eddade-a2dc-4d16-8710-fb764d...   
3                      29/120200233302/1030010006CA6400   
4                      29/120202011123/1030010006CA6400   
...                                                 ...   
8719  29/120202001113/69ba0f63-4e24-41b8-bdac-7de80a...   
8720  29/120202001321/f9e104a1-aab0-400b-a938-66897c...   
8721  29/120202001130/f9e104a1-aab0-400b-a938-66897c...   
8722                   29/120202011321/10500500F3DD9500   
8723                   29/120202012001/1050050044DEB300   

                                                   type         title  \
0     image/tiff; application=geotiff; profile=cloud...  Visual Image   
1     image/tiff; application=geotiff; profile=cloud...  Visual Image   
2     image/tiff; application=geotiff; profile=cloud...  Visual Image   
3     image/tiff; application=geotiff; profile=cloud...  Visual Image   
4     image/tiff; application=geotiff; profile=cloud...  Visual Image   
...                                                 ...           ...   
8719  image/tiff; application=geotiff; profile=cloud...  Visual Image   
8720  image/tiff; application=geotiff; profile=cloud...  Visual Image   
8721  image/tiff; application=geotiff; profile=cloud...  Visual Image   
8722  image/tiff; application=geotiff; profile=cloud...  Visual Image   
8723  image/tiff; application=geotiff; profile=cloud...  Visual Image   

                                                   href              datetime  \
0     https://maxar-opendata.s3.amazonaws.com/events...  2018-08-31 11:25:53Z   
1     https://maxar-opendata.s3.amazonaws.com/events...  2018-08-31 11:25:49Z   
2     https://maxar-opendata.s3.amazonaws.com/events...  2018-08-31 11:25:52Z   
3     https://maxar-opendata.s3.amazonaws.com/events...  2010-08-26 11:38:33Z   
4     https://maxar-opendata.s3.amazonaws.com/events...  2010-08-26 11:38:36Z   
...                                                 ...                   ...   
8719  https://maxar-opendata.s3.amazonaws.com/events...  2018-08-20 11:49:04Z   
8720  https://maxar-opendata.s3.amazonaws.com/events...  2018-08-26 11:44:38Z   
8721  https://maxar-opendata.s3.amazonaws.com/events...  2018-08-26 11:44:41Z   
8722  https://maxar-opendata.s3.amazonaws.com/events...  2021-09-22 11:29:50Z   
8723  https://maxar-opendata.s3.amazonaws.com/events...  2023-02-09 11:31:38Z   

     platform   gsd                                catalog_id  utm_zone  \
0        WV04  0.36  04eddade-a2dc-4d16-8710-fb764d318766-inv        29   
1        WV04  0.36  04eddade-a2dc-4d16-8710-fb764d318766-inv        29   
2        WV04  0.37  04eddade-a2dc-4d16-8710-fb764d318766-inv        29   
3        WV02  0.48                          1030010006CA6400        29   
4        WV02  0.49                          1030010006CA6400        29   
...       ...   ...                                       ...       ...   
8719     WV04  0.39  69ba0f63-4e24-41b8-bdac-7de80adc868c-inv        29   
8720     WV04  0.35  f9e104a1-aab0-400b-a938-66897c77e7d3-inv        29   
8721     WV04  0.35  f9e104a1-aab0-400b-a938-66897c77e7d3-inv        29   
8722     GE01  0.48                          10500500F3DD9500        29   
8723     GE01  0.49                          1050050044DEB300        29   

           quadkey  view_off_nadir  view_azimuth  view_incidence_angle  \
0     031313133311       24.400000    121.500000                  63.1   
1     031313311112       23.299999    111.300003                  64.3   
2     031313133301       24.900000    120.300003                  62.5   
3     120200233302       12.200000    284.899994                  76.3   
4     120202011123       13.100000    287.100006                  75.3   
...            ...             ...           ...                   ...   
8719  120202001113       29.400000    274.700012                  57.4   
8

In [12]:
maxar_items.platform.value_counts()

platform
WV03    4626
WV02    2830
GE01    1028
WV04     240
Name: count, dtype: int64

In [13]:
maxar_items.groupby(["platform", "after_event"]).size()

platform  after_event
GE01      0              1028
WV02      0              2434
          1               396
WV03      0              4537
          1                89
WV04      0               240
dtype: int64

In [16]:
print(maxar_items.datetime.min()) 
print(maxar_items.datetime.max())

2010-06-02 11:32:07Z
2023-09-11 11:08:54Z


In [21]:
maxar_items[]

0       2018-08-31 11:25:53Z
1       2018-08-31 11:25:49Z
2       2018-08-31 11:25:52Z
3       2010-08-26 11:38:33Z
4       2010-08-26 11:38:36Z
                ...         
8719    2018-08-20 11:49:04Z
8720    2018-08-26 11:44:38Z
8721    2018-08-26 11:44:41Z
8722    2021-09-22 11:29:50Z
8723    2023-02-09 11:31:38Z
Name: datetime, Length: 8724, dtype: object

In [31]:
wv02_after_event = maxar_items[(maxar_items.platform == "WV02") & (maxar_items.after_event == 0)]

In [32]:
town

town_name                        geometry
0      Adassil  POINT (547909.130 3441974.137)
1  Tafeghaghte  POINT (573971.703 3451595.559)
2       Mejdid  POINT (548561.849 3442843.085)
3         Amzi  POINT (575844.024 3451538.007)
4      Tinzert  POINT (594423.730 3451056.954)
5    Taroudant  POINT (512035.792 3371260.816)

In [33]:
m = wv02_after_event.explore()
town.explore(m=m, color="red", marker_type="marker")

In [25]:
name = "Adassil"
df_tafe = gpd.read_file(os.path.join(out_dir_path, name, f"maxar_items_{name}.shp"))
#df_tafe[(df_tafe.after_even == 0) & (df_tafe.platform =="WV02")]["href"].values

In [27]:
df_tafe[df_tafe.platform =="WV02"][["platform","datetime","gsd", "view_off_n", "view_azimu", "view_incid", "view_sun_a", "view_sun_e", "after_even"]]

platform              datetime   gsd  view_off_n  view_azimu  view_incid  \
0     WV02  2023-09-10 11:44:26Z  0.64   32.700001  305.200012        52.8   
1     WV02  2018-08-09 11:27:38Z  0.49   13.700000   47.099998        74.6   

   view_sun_a  view_sun_e  after_even  
0       154.9        61.8           1  
1       128.7        67.7           0

In [31]:
df_tafe[["platform","datetime","gsd", "view_off_n", "view_azimu", "view_incid", "view_sun_a", "view_sun_e", "utm_zone", "proj_epsg",  "after_even"]]

platform              datetime   gsd  view_off_n  view_azimu  view_incid  \
0     WV02  2023-09-10 11:44:26Z  0.64   32.700001  305.200012        52.8   
1     WV02  2018-08-09 11:27:38Z  0.49   13.700000   47.099998        74.6   
2     WV03  2019-07-16 11:53:40Z  0.38   28.200001  283.899994        58.8   
3     WV03  2023-07-14 11:15:22Z  0.33   16.799999   53.299999        71.5   
4     WV03  2023-07-14 11:16:14Z  0.35   22.400000  162.600006        65.3   
5     GE01  2022-08-28 11:16:44Z  0.43   15.200000   96.300003        73.2   

   view_sun_a  view_sun_e  utm_zone  proj_epsg  after_even  
0       154.9        61.8        29      32629           1  
1       128.7        67.7        29      32629           0  
2       129.7        75.8        29      32629           0  
3       111.0        69.0        29      32629           0  
4       111.3        69.2        29      32629           0  
5       135.2        61.9        29      32629           0

In [29]:
df_tafe.columns

Index(['id', 'type', 'title', 'href', 'datetime', 'platform', 'gsd',
       'catalog_id', 'utm_zone', 'quadkey', 'view_off_n', 'view_azimu',
       'view_incid', 'view_sun_a', 'view_sun_e', 'proj_epsg', 'grid_code',
       'data_area', 'clouds_are', 'clouds_per', 'geometry_b', 'after_even',
       'town_name', 'intersec_r', 'geometry'],
      dtype='object')

Does tif file keep meta data ?

### Pipeline

In [12]:
# extract (clip) roi rs on town buffer

In [13]:
def load_maxar_items(): 
    columns = load_pickle(make_path("mapping_columns_stac_collection.pkl", out_dir_path))
    maxar_items = gpd.read_file(make_path("maxar_stac_items.shp", out_dir_path)).rename(columns, axis=1)
    return maxar_items

def load_roi_town():
    return gpd.read_file(make_path("marocco_town.shp", raw_data_path))

In [14]:
town_test = "Adassil"

roi_test = town[town.town_name ==town_test]
roi_test.geometry = [box(*_.bounds) for _ in roi_test.buffer(500)]

In [22]:
roi_test

town_name                                           geometry
0   Adassil  POLYGON ((548409.130 3441474.137, 548409.130 3...

In [49]:
def crop_rs_on_shape(rs_path: str, shape: Union[Polygon, List], out_path: str):
    """
    Crop raster from shapely geometry shape

    - add check crs equality
    - clip_box with rioxarray => pyproj CRS error
    
    """
    if not isinstance(shape, list):
        shape = [shape]
        
    with rio.open(rs_path) as src:
        out_image, out_transform = rio.mask.mask(src, shape, crop=True)
        out_meta = src.meta
    
        out_meta.update({"driver": "GTiff",
                     "height": out_image.shape[1],
                     "width": out_image.shape[2],
                     "transform": out_transform})
    
        with rio.open(out_path, "w", **out_meta) as dest:
            dest.write(out_image)

In [56]:
def compute_intersection(shp_rs, shp_roi):
    assert shp_rs.crs == shp_roi.crs
    shp_rs = gpd.overlay(shp_rs, shp_roi, how='intersection')
    shp_rs["intersec_roi_perc"] = shp_rs.area / shp_roi.area.item()
    return shp_rs

def download_maxar_on_roi(town_geom=None, 
                town_name=None, 
                th_intersect=0.90, 
                date_event='2023-09-09'): 

    maxar_items = load_maxar_items()
    maxar_items = maxar_items.assign(
        after_event=(maxar_items.datetime > date_event)*1
    )
    town = load_roi_town()  
    for name in town.town_name.unique():
        print(f"==== TOWN : {name} =====")
        
        town_buffer_df = town[town.town_name == name]    
        town_buffer_df.geometry = [box(*_.bounds) for _ in town_buffer_df.buffer(500)]
        
        bbox_buffer = box(*town_buffer_df.bounds.values.squeeze())

        items_town = compute_intersection(maxar_items, town_buffer_df)
        items_town = items_town[items_town.intersec_roi_perc > 0.9]
        
        # order by date to be sur to get both before and after - workaround
        items_town = items_town.sort_values("after_event", ascending=False)
        print(f"found {items_town.shape[0]} maxar items")

        if not os.path.exists(os.path.join(out_dir_path, name)):
             os.mkdir(os.path.join(out_dir_path, name))
        path_town_dir = os.path.join(out_dir_path, name)
        
        items_town.to_file(os.path.join(path_town_dir, f"maxar_items_{name}.shp"))
        
        cnt = 0
        for i, row in items_town.iterrows():
            if cnt == 5:
                # stop download after 5 tiles per town
                break


            delta_event = "after" if row["after_event"] == 1 else "before"
            
            if not os.path.exists(os.path.join(path_town_dir, delta_event)):
                os.mkdir(os.path.join(path_town_dir, delta_event))
                
            path_rs = os.path.join(path_town_dir, delta_event)

            """
            select "last before" tile
            """

            path_tmp_rs = os.path.join(path_rs, "full_rs_tmp.tif")
            
            leafmap.download_file(row["href"], output=path_tmp_rs, overwrite=False)
            
            path_rs_clip = os.path.join(path_rs,row["href"].split("/")[-1])

            try:
                rs_roi = crop_rs_on_shape(path_tmp_rs, bbox_buffer, path_rs_clip)
            except:
                print(f"erreur : {i} : {path_tmp_rs}")

            print(f"Save {path_rs_clip} for {name} : {delta_event} event {row['datetime']}")

            # delete full rs
            os.remove(path_tmp_rs)
            cnt+=1
        print(f"Downloaded {cnt} images for {name}")
    print(f"=== End downloads ====")

In [53]:
res

In [57]:
%%time
res = download_maxar_on_roi(th_intersect=0.90, 
            date_event='2023-09-09'
           )

==== TOWN : Adassil =====
found 6 maxar items


Downloading...
From: https://maxar-opendata.s3.amazonaws.com/events/Morocco-Earthquake-Sept-2023/ard/29/120202003223/2023-09-10/10300500E4F91500-visual.tif
To: /home/rustt/Documents/Projects/building_damage/Data/processed/Adassil/after/full_rs_tmp.tif

  0%|                                                       | 0.00/73.2M [00:00<?, ?B/s]
  1%|▎                                               | 524k/73.2M [00:00<01:35, 758kB/s]
  1%|▋                                             | 1.05M/73.2M [00:00<00:58, 1.22MB/s]
  2%|▉                                             | 1.57M/73.2M [00:01<00:39, 1.83MB/s]
  4%|█▋                                            | 2.62M/73.2M [00:01<00:43, 1.64MB/s]
  7%|███▎                                          | 5.24M/73.2M [00:01<00:15, 4.35MB/s]
  9%|███▉                                          | 6.29M/73.2M [00:02<00:20, 3.29MB/s]
 11%|████▉                                         | 7.86M/73.2M [00:02<00:14, 4.51MB/s]
 12%|█████▌                        

Save /home/rustt/Documents/Projects/building_damage/Data/processed/Adassil/after/10300500E4F91500-visual.tif for Adassil : after event 2023-09-10 11:44:26Z


Downloading...
From: https://maxar-opendata.s3.amazonaws.com/events/Morocco-Earthquake-Sept-2023/ard/29/120202003223/2018-08-09/1030010083A10700-visual.tif
To: /home/rustt/Documents/Projects/building_damage/Data/processed/Adassil/before/full_rs_tmp.tif

  0%|                                                       | 0.00/45.3M [00:00<?, ?B/s]
  1%|▌                                               | 524k/45.3M [00:00<00:59, 751kB/s]
  2%|█                                             | 1.05M/45.3M [00:00<00:34, 1.30MB/s]
  3%|█▌                                            | 1.57M/45.3M [00:01<00:24, 1.82MB/s]
  6%|██▋                                           | 2.62M/45.3M [00:01<00:14, 2.98MB/s]
  7%|███▏                                          | 3.15M/45.3M [00:01<00:21, 2.00MB/s]
 13%|█████▊                                        | 5.77M/45.3M [00:01<00:07, 5.01MB/s]
 15%|██████▉                                       | 6.82M/45.3M [00:02<00:08, 4.58MB/s]
 17%|███████▉                     

Save /home/rustt/Documents/Projects/building_damage/Data/processed/Adassil/before/1030010083A10700-visual.tif for Adassil : before event 2018-08-09 11:27:38Z


...

Save /home/rustt/Documents/Projects/building_damage/Data/processed/Taroudant/before/104001003FAD9700-visual.tif for Taroudant : before event 2018-07-29 11:50:31Z


Downloading...
From: https://maxar-opendata.s3.amazonaws.com/events/Morocco-Earthquake-Sept-2023/ard/29/120202022212/2019-04-25/1040010049533A00-visual.tif
To: /home/rustt/Documents/Projects/building_damage/Data/processed/Taroudant/before/full_rs_tmp.tif

  0%|                                                       | 0.00/66.4M [00:00<?, ?B/s]
  1%|▍                                               | 524k/66.4M [00:03<08:06, 135kB/s]
  2%|▋                                              | 1.05M/66.4M [00:06<06:08, 177kB/s]
  2%|█                                              | 1.57M/66.4M [00:07<04:26, 243kB/s]
  3%|█▍                                             | 2.10M/66.4M [00:08<03:18, 324kB/s]
  4%|█▊                                             | 2.62M/66.4M [00:08<02:29, 427kB/s]
  5%|██▏                                            | 3.15M/66.4M [00:09<01:58, 535kB/s]
  6%|██▌                                            | 3.67M/66.4M [00:09<01:33, 672kB/s]
  6%|██▉                        

Save /home/rustt/Documents/Projects/building_damage/Data/processed/Taroudant/before/1040010049533A00-visual.tif for Taroudant : before event 2019-04-25 11:50:48Z


Downloading...
From: https://maxar-opendata.s3.amazonaws.com/events/Morocco-Earthquake-Sept-2023/ard/29/120202022212/2019-03-25/1040010049D28B00-visual.tif
To: /home/rustt/Documents/Projects/building_damage/Data/processed/Taroudant/before/full_rs_tmp.tif

  0%|                                                       | 0.00/76.5M [00:00<?, ?B/s]
  1%|▎                                               | 524k/76.5M [00:04<09:58, 127kB/s]
  1%|▋                                              | 1.05M/76.5M [00:06<07:26, 169kB/s]
  2%|▉                                              | 1.57M/76.5M [00:07<05:10, 241kB/s]
  3%|█▎                                             | 2.10M/76.5M [00:08<03:51, 321kB/s]
  3%|█▌                                             | 2.62M/76.5M [00:08<02:58, 415kB/s]
  4%|█▉                                             | 3.15M/76.5M [00:09<02:14, 545kB/s]
  5%|██▎                                            | 3.67M/76.5M [00:09<01:49, 665kB/s]
  5%|██▌                        

Save /home/rustt/Documents/Projects/building_damage/Data/processed/Taroudant/before/1040010049D28B00-visual.tif for Taroudant : before event 2019-03-25 11:57:09Z
Downloaded 5 images for Taroudant
=== End downloads ====
CPU times: user 23.2 s, sys: 24.1 s, total: 47.3 s
Wall time: 8min 48s


### Number of images per Town

In [ ]:
cnt_town = 
path_town_dir = os.path.join(out_dir_path, name)


In [14]:
town[town.town_name == "Tafeghaghte"].geometry.buffer(200).bounds.values.squeeze()

array([ 573771.7033168 , 3451395.55870075,  574171.7033168 ,
       3451795.55870075])

### Remarques
* buffer too large

In [18]:
rs_path = os.path.join(out_dir_path, "Tafeghaghte", "before", "10400100405FEB00-visual.tif")
buffer_size = 100
bbox_coords = town[town.town_name == "Tafeghaghte"].geometry.buffer(buffer_size).bounds.values.squeeze()
shape = [box(*bbox_coords)]
out_path = os.path.join(out_dir_path, "Tafeghaghte", f"clip_buf_{buffer_size}.tif")

with rio.open(rs_path) as src:
    out_image, out_transform = rio.mask.mask(src, shape, crop=True)
    out_meta = src.meta

    out_meta.update({"driver": "GTiff",
                 "height": out_image.shape[1],
                 "width": out_image.shape[2],
                 "transform": out_transform})

    with rio.open(out_path, "w", **out_meta) as dest:
        dest.write(out_image)

In [1]:
town

NameError: name 'town' is not defined

### Details

In [31]:
maxar_items.after_event.value_counts()

after_event
0    8239
1     485
Name: count, dtype: int64

In [32]:
roi_items = maxar_items.sjoin(town)

In [37]:
roi_items[roi_items.town_name == "Adassil"].platform

826     WV02
2575    WV02
4447    WV03
6793    WV03
6830    WV03
8132    GE01
Name: platform, dtype: object

In [35]:
roi_items.groupby(["town_name", "platform", "after_event"]).size()

town_name    platform  after_event
Adassil      GE01      0              1
             WV02      0              1
                       1              1
             WV03      0              3
Amzi         WV02      1              2
             WV03      0              2
Mejdid       GE01      0              1
             WV02      0              1
                       1              1
             WV03      0              3
Tafeghaghte  WV02      1              2
             WV03      0              3
Taroudant    GE01      0              1
             WV02      1              1
             WV03      0              9
Tinzert      WV02      1              1
             WV03      0              1
dtype: int64

In [41]:
roi_test = roi_items[roi_items.town_name == town_test]

In [42]:
roi_test.after_event.value_counts()

after_event
0    3
1    2
Name: count, dtype: int64

In [43]:
roi_test.datetime

2125    2023-09-10 11:46:14Z
2731    2023-09-11 11:08:47Z
3439    2018-08-17 11:52:14Z
3701    2018-12-19 11:29:07Z
5847    2022-05-12 11:35:57Z
Name: datetime, dtype: object

In [44]:
roi_test_before = roi_test[roi_test.after_event == 0].sort_values("datetime", ascending=False).head(1)
roi_test_after = roi_test[roi_test.after_event == 1].sample()

In [45]:
roi_test_before

id  \
5847  29/120202003312/10400100797DAC00   

                                                   type         title  \
5847  image/tiff; application=geotiff; profile=cloud...  Visual Image   

                                                   href              datetime  \
5847  https://maxar-opendata.s3.amazonaws.com/events...  2022-05-12 11:35:57Z   

     platform   gsd        catalog_id  utm_zone       quadkey  view_off_nadir  \
5847     WV03  0.39  10400100797DAC00        29  120202003312            28.9   

      view_azimuth  view_incidence_angle  view_sun_azimuth  \
5847    308.100006                  58.0             133.4   

      view_sun_elevation  proj_epsg              grid_code  data_area  \
5847                72.3      32629  MXRA-Z29-120202003312   25.90625   

      clouds_area  clouds_percent  \
5847          0.0             0.0   

                                          geometry_bbox  \
5847  [569843.75, 3449843.75, 574797.36328125, 34551...   

                                               geometry  after_event  \
5847  POLYGON ((569843.750 3455156.250, 574797.363 3...            0   

      index_right    town_name  dummy  
5847            1  Tafeghaghte      1

In [47]:
roi_test_after

id  \
2731  29/120202003312/10300500E4F92300   

                                                   type         title  \
2731  image/tiff; application=geotiff; profile=cloud...  Visual Image   

                                                   href              datetime  \
2731  https://maxar-opendata.s3.amazonaws.com/events...  2023-09-11 11:08:47Z   

     platform   gsd        catalog_id  utm_zone       quadkey  view_off_nadir  \
2731     WV02  0.55  10300500E4F92300        29  120202003312       24.799999   

      view_azimuth  view_incidence_angle  view_sun_azimuth  \
2731         115.0                  61.9             140.3   

      view_sun_elevation  proj_epsg              grid_code  data_area  \
2731                57.4      32629  MXRA-Z29-120202003312  28.203125   

      clouds_area  clouds_percent  \
2731          0.0             0.0   

                                       geometry_bbox  \
2731  [569843.75, 3449843.75, 575156.25, 3455156.25]   

                                               geometry  after_event  \
2731  POLYGON ((569843.750 3455156.250, 575156.250 3...            1   

      index_right    town_name  dummy  
2731            1  Tafeghaghte      1